# Review: Continuations, CPS

This notebook summarizes our exploration into Continuation-Passing Style (CPS) in Python.

Consider the old favorite, factorial, written with standard recursion:

In [1]:
def fact(n):
    if n == 1:
        return 1
    else:
        return n * fact(n - 1)

In [2]:
fact(5)

120

In [3]:
print fact(976)

5314465955234328433095956556316762869180467000711204019511211394992252608087797082539037344385795907890015671532564990269745321452081220878736433133062382891890706236582696985430165474027795918886498215689470959674968200220151438149912983216237245867362429297314485827245238782553435010966872653763032393610259187517706444016252693189983494913715138456699860163710392033585467757433092631122578027336445157361611582772005936415844681633910315087092559255317204324173993974425864903511892230518574773222327845556202639620802112949805936893483540746426414190657702599979652787665626954744147840296017310321928878532796971683095103218341588688398321601944592324705357739355528284279394381399201748530662561573374752652214136890556598215146201591387373819034719308391735677849846086523385715008368586298349934894206960737706799585056775007065430754581962232329930998668240560616565303752495572660735440020628323040700208543940955990097315718255037105159462456160864678749853271135068155539126651219092118

This works, in Python!

But this type of code will fail in languages like C and Java for a completely different reason: you will "overflow" the bits that a number can contain. We'll discuss `types` later. But for now, realize that both Scheme and Python do a smart thing here: they automatically switch from `Integers` to `BigNums` (a data structure-based number representation).

But if we try to compute just one more:

In [4]:
try:
    print fact(977)
except:
    print "Fail!"

Fail!


Why?

In [5]:
try:
    print fact(977)
except Exception as e:
    print e.message

maximum recursion depth exceeded


This is the problem that we are exploring with continuations and CPS.

We can rewrite fact in CPS. Here, we use functions to represent continuations. So in this example, a continuation is a function that takes a value. When you get a result, you "pass it to the continuation"... meaning that since the continuation is a function, you simply "call" the continuation with the result as an argument.

Recall the three steps of CPS transformation:
    
1. Add a continuation, k, to the recursive function
2. Give any result to the continuation
3. Any computation that is left to do after a recursive call must be done in a new continuation

In [6]:
def fact_cps(n, k):
    if n == 1:
        return k(1)
    else:
        return fact_cps(n - 1,
                        lambda v: k(v * n))

In [7]:
fact_cps(2, lambda i: i)

2

And give the identity function as the initial continuation:

In [8]:
fact_cps(5, lambda i: i)

120

Yet:

In [9]:
try:
    print fact_cps(1000, lambda i: i)
except Exception as e:
    print e.message

maximum recursion depth exceeded


The first thing we can do is move the "calling of the continuation" out from inside the recursive function:

In [10]:
def fact_cps(n, k):
    if n == 1:
        return ["apply-cont", k, 1]
    else:
        return fact_cps(n - 1,
                        lambda v: ["apply-cont", k, v * n])

And then make a "trampoline" to run it:

In [11]:
def trampoline(result):
    while isinstance(result, list):
        result = result[1](result[2])
    return result

In [12]:
trampoline(fact_cps(5, lambda i: i))

120

Yet:

In [13]:
try:
    print trampoline(fact_cps(1000, lambda i: i))
except Exception as e:
    print e.message

maximum recursion depth exceeded


The problem is that we are still calling the recursive function recursively. We can move out the recursive call, similarly to what we did with the calling of the continuation. 

We note that after we have transformed a function into CPS, the rest of the computation could be carried out by a simple GOTO. We approximate this by returning a "goto" list that contains the name of the function, and its arguments. Really, we are just moving the "calling of the recursive function" from inside the recursive function to the trampoline:

In [14]:
def fact_cps(n, k):
    if n == 1:
        return ["apply-cont", k, 1]
    else:
        return ["goto", fact_cps, n - 1,
                        lambda v: ["apply-cont", k, v * n]]

In [15]:
def trampoline(result):
    while isinstance(result, list):
        if result[0] == "apply-cont":
            result = result[1](result[2])
        elif result[0] == "goto":
            result = apply(result[1], result[2:])
    return result

Thus, we have three things that calling a recursive CPS function can return:

* a continuation
* a goto, a recursive call
* a result

The trampoline will bounce through these until a result is gotten:

In [16]:
try:
    print trampoline(fact_cps(1000, lambda i: i))
except Exception as e:
    print e.message

4023872600770937735437024339230039857193748642107146325437999104299385123986290205920442084869694048004799886101971960586316668729948085589013238296699445909974245040870737599188236277271887325197795059509952761208749754624970436014182780946464962910563938874378864873371191810458257836478499770124766328898359557354325131853239584630755574091142624174743493475534286465766116677973966688202912073791438537195882498081268678383745597317461360853795345242215865932019280908782973084313928444032812315586110369768013573042161687476096758713483120254785893207671691324484262361314125087802080002616831510273418279777047846358681701643650241536913982812648102130927612448963599287051149649754199093422215668325720808213331861168115536158365469840467089756029009505376164758477284218896796462449451607653534081989013854424879849599533191017233555566021394503997362807501378376153071277619268490343526252000158885351473316117021039681759215109077880193931781141945452572238655414610628921879602238389714760

At this point, there is no stack!

That doesn't mean we can compute the factorial of any huge number... fact_cps still takes memory in the form of a continuation for each recursion. But there are no more stack limits to hold us back!

On the other hand, some recursions can now run forever, because they don't take any more continuations. Consider:

In [17]:
def loop():
    return loop()

In [18]:
try:
    loop()
except:
    print "Fail!"

Fail!


But we can do the same tricks:

In [19]:
def loop_cps(k):
    return ["goto", loop_cps, k]

In [20]:
trampoline(loop_cps(lambda i: i))

KeyboardInterrupt: 

(I had to press the Interrupt button to stop, as this would run forever)

Handling multiple recursions can get a little tricky, but is still very mechanical. Consider fib:

In [21]:
def fib(n):
    if n == 0:
        return 1
    elif n == 1:
        return 1
    else:
        return fib(n - 1) + fib(n - 2)

In [22]:
fib(5)

8

Again, the three steps of CPS transformation:
    
1. Add a continuation, k, to the recursive function
2. Give any result to the continuation
3. Any computation that is left to do after a recursive call must be done in a new continuation

First, we write it in standard CPS form:

In [23]:
def fib_cps(n, k):
    if n == 0:
        return k(1)
    elif n == 1:
        return k(1)
    else:
        return fib_cps(n - 1, 
                lambda v1: fib_cps(n - 2,
                            lambda v2: k(v1 + v2)))

In [24]:
fib_cps(5, lambda i: i)

8

Then, we "unroll" the function calls so that they are done in the trampoline: 

In [25]:
def fib_cps(n, k):
    if n == 0:
        return ["apply-cont", k, 1]
    elif n == 1:
        return ["apply-cont", k, 1]
    else:
        return ["goto", fib_cps, n - 1, 
                lambda v1: ["goto", fib_cps, n - 2,
                            lambda v2: ["apply-cont", k, v1 + v2]]]

In [26]:
trampoline(fib_cps(5, lambda i: i))

8

This will take forever for numbers over 20 something. Why? Not because it is recursive, but because it is stupidly re-computing things over and over.

Don't confuse recursion with stupidity! Recursion is often the right tool for the job, especially if you have a recursive data structure, and are working an appropriate programming language. 